In [1]:
import tensorflow as tf
from tensorflow import keras
print(tf.__version__)

print(keras.__version__)

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import os

ImportError: Traceback (most recent call last):
  File "C:\Users\admin\anaconda3\lib\site-packages\tensorflow\python\pywrap_tensorflow.py", line 58, in <module>
    from tensorflow.python.pywrap_tensorflow_internal import *
  File "C:\Users\admin\anaconda3\lib\site-packages\tensorflow\python\pywrap_tensorflow_internal.py", line 28, in <module>
    _pywrap_tensorflow_internal = swig_import_helper()
  File "C:\Users\admin\anaconda3\lib\site-packages\tensorflow\python\pywrap_tensorflow_internal.py", line 24, in swig_import_helper
    _mod = imp.load_module('_pywrap_tensorflow_internal', fp, pathname, description)
  File "C:\Users\admin\anaconda3\lib\imp.py", line 242, in load_module
    return load_dynamic(name, filename, file)
  File "C:\Users\admin\anaconda3\lib\imp.py", line 342, in load_dynamic
    return _load(spec)
ImportError: DLL load failed: Nie można odnaleźć określonego modułu.


Failed to load the native TensorFlow runtime.

See https://www.tensorflow.org/install/errors

for s

In [32]:
# Wczytaj dane treningowe i testowe
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

train_set = pd.read_csv('Dane/adult/adult.data', sep=", ",header = None)
test_set = pd.read_csv('Dane/adult/adult.test', sep=", ",skiprows = 1, header = None) # Make sure to skip a row for the test set

col_labels = ['age', 'workclass', 'fnlwgt', 'education', 'education_num', 'marital_status', 'occupation', 
              'relationship', 'race', 'sex', 'capital_gain', 'capital_loss', 'hours_per_week', 'native_country',
             'wage_class']
train_set.columns = col_labels
test_set.columns = col_labels

train = train_set.replace('?', np.nan).dropna()
test = test_set.replace('?', np.nan).dropna()

train_set.head()

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:6: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  import sys


age         workclass  fnlwgt  education  education_num  \
0   39         State-gov   77516  Bachelors             13   
1   50  Self-emp-not-inc   83311  Bachelors             13   
2   38           Private  215646    HS-grad              9   
3   53           Private  234721       11th              7   
4   28           Private  338409  Bachelors             13   

       marital_status         occupation   relationship   race     sex  \
0       Never-married       Adm-clerical  Not-in-family  White    Male   
1  Married-civ-spouse    Exec-managerial        Husband  White    Male   
2            Divorced  Handlers-cleaners  Not-in-family  White    Male   
3  Married-civ-spouse  Handlers-cleaners        Husband  Black    Male   
4  Married-civ-spouse     Prof-specialty           Wife  Black  Female   

   capital_gain  capital_loss  hours_per_week native_country wage_class  
0          2174             0              40  United-States      <=50K  
1             0             0              13  United-States      <=50K  
2             0             0              40  United-States      <=50K  
3             0             0              40  United-States      <=50K  
4             0             0              40           Cuba      <=50K

In [33]:
dataset = pd.concat([train,test])

dataset['wage_class'] = dataset.wage_class.replace({'<=50K.': 0,'<=50K':0, '>50K.':1, '>50K':1})

dataset.drop(["fnlwgt"],axis=1,inplace=True)

dataset.drop(["education"],axis=1,inplace=True)

x = dataset.groupby('native_country')["wage_class"].mean()

d = dict(pd.cut(x[x.index!=" United-States"],5,labels=range(5)))

dataset['native_country'] = dataset['native_country'].replace(d)

dataset = pd.get_dummies(dataset,drop_first=True)

train = dataset.iloc[:train.shape[0]]
test = dataset.iloc[train.shape[0]:]

X_train = train.drop("wage_class",axis=1)
y_train = train.wage_class

X_test = test.drop("wage_class",axis=1)
y_test = test.wage_class

from sklearn.preprocessing import StandardScaler
sc = StandardScaler()
X_train = sc.fit_transform(X_train)
X_test = sc.transform(X_test)

print(X_train.shape)
print(X_test.shape)

(30162, 41)
(15060, 41)


In [54]:
keras.backend.clear_session()

def build_model(n_hidden=1, n_neurons=30, learning_rate=3e-3, input_shape=[41,]):
    model = keras.models.Sequential()
    model.add(keras.layers.InputLayer(input_shape=input_shape))
    for layer in range(n_hidden):
        model.add(keras.layers.Dense(n_neurons, activation="relu"))
    model.add(keras.layers.Dense(1))
    optimizer = keras.optimizers.SGD(lr=learning_rate)
    model.compile(loss="binary_crossentropy", optimizer=optimizer, metrics=["accuracy"])
    return model

In [55]:
keras_class = tf.keras.wrappers.scikit_learn.KerasClassifier(build_model)
keras_class

In [56]:
from keras.callbacks import EarlyStopping
keras_class.fit(X_train, y_train, epochs=100, validation_split=0.1, callbacks=[EarlyStopping(monitor='val_loss', patience=10, mode='min', verbose=1)])

Train on 27145 samples, validate on 3017 samples
Epoch 1/100
27145/27145 [==============================] - 2s 61us/sample - loss: 2.3350 - accuracy: 0.7434 - val_loss: 6.3700 - val_accuracy: 0.5449
Epoch 2/100
27145/27145 [==============================] - 1s 44us/sample - loss: 4.2137 - accuracy: 0.7111 - val_loss: 3.9316 - val_accuracy: 0.7451
Epoch 3/100
27145/27145 [==============================] - 1s 41us/sample - loss: 3.8294 - accuracy: 0.7517 - val_loss: 3.9316 - val_accuracy: 0.7451
Epoch 4/100
27145/27145 [==============================] - 1s 40us/sample - loss: 3.8294 - accuracy: 0.7517 - val_loss: 3.9316 - val_accuracy: 0.7451
Epoch 5/100
27145/27145 [==============================] - 1s 41us/sample - loss: 3.8294 - accuracy: 0.7517 - val_loss: 3.9316 - val_accuracy: 0.7451
Epoch 6/100
27145/27145 [==============================] - 1s 40us/sample - loss: 3.8294 - accuracy: 0.7517 - val_loss: 3.9316 - val_accuracy: 0.7451
Epoch 7/100
27145/27145 [==========================

# Zad

Wykonajmy RandomizedSearchCV

In [59]:
from scipy.stats import reciprocal
from sklearn.model_selection import RandomizedSearchCV

param_distribs = {
    "n_hidden": [0, 1, 2, 3],
    "n_neurons": np.arange(1, 100)
}

rnd_search_cv = RandomizedSearchCV(keras_class, param_distribs, n_iter=10, cv=3, verbose=2)
rnd_search_cv.fit(X_train, y_train, epochs=100, validation_split=0.1, callbacks=[EarlyStopping(monitor='val_loss', patience=10, mode='min', verbose=1)])

Fitting 3 folds for each of 10 candidates, totalling 30 fits
[CV] n_neurons=3, n_hidden=1 .........................................
Train on 18097 samples, validate on 2011 samples
Epoch 1/100


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


18097/18097 [==============================] - 1s 63us/sample - loss: 3.8475 - accuracy: 0.7506 - val_loss: 4.0729 - val_accuracy: 0.7360
Epoch 2/100
18097/18097 [==============================] - 1s 41us/sample - loss: 3.8475 - accuracy: 0.7506 - val_loss: 4.0729 - val_accuracy: 0.7360
Epoch 3/100
18097/18097 [==============================] - 1s 40us/sample - loss: 3.8475 - accuracy: 0.7506 - val_loss: 4.0729 - val_accuracy: 0.7360
Epoch 4/100
18097/18097 [==============================] - 1s 41us/sample - loss: 3.8475 - accuracy: 0.7506 - val_loss: 4.0729 - val_accuracy: 0.7360
Epoch 5/100
18097/18097 [==============================] - 1s 42us/sample - loss: 3.8475 - accuracy: 0.7506 - val_loss: 4.0729 - val_accuracy: 0.7360
Epoch 6/100
18097/18097 [==============================] - 1s 39us/sample - loss: 3.8475 - accuracy: 0.7506 - val_loss: 4.0729 - val_accuracy: 0.7360
Epoch 7/100
18097/18097 [==============================] - 1s 41us/sample - loss: 3.8475 - accuracy: 0.7506 - va

[CV] .......................... n_neurons=3, n_hidden=1, total=   9.2s
[CV] n_neurons=3, n_hidden=1 .........................................
Train on 18097 samples, validate on 2011 samples
Epoch 1/100


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    9.1s remaining:    0.0s


...

[CV] ......................... n_neurons=19, n_hidden=2, total=  13.5s
[CV] n_neurons=19, n_hidden=2 ........................................
Train on 18097 samples, validate on 2011 samples
Epoch 1/100
18097/18097 [==============================] - 1s 71us/sample - loss: 2.9491 - accuracy: 0.7230 - val_loss: 3.5349 - val_accuracy: 0.7146
Epoch 2/100
18097/18097 [==============================] - 1s 46us/sample - loss: 3.0298 - accuracy: 0.7626 - val_loss: 2.3030 - val_accuracy: 0.7956
Epoch 3/100
18097/18097 [==============================] - 1s 44us/sample - loss: 2.5093 - accuracy: 0.7958 - val_loss: 3.1426 - val_accuracy: 0.7772
Epoch 4/100
18097/18097 [==============================] - 1s 47us/sample - loss: 3.0167 - accuracy: 0.7810 - val_loss: 4.5653 - val_accuracy: 0.6892
Epoch 5/100
18097/18097 [==============================] - 1s 54us/sample - loss: 4.1666 - accuracy: 0.7052 - val_loss: 3.8759 - val_accuracy: 0.7166
Epoch 6/100
18097/18097 [==============================] - 

[CV] ......................... n_neurons=19, n_hidden=2, total=  39.8s
[CV] n_neurons=19, n_hidden=2 ........................................
Train on 18097 samples, validate on 2011 samples
Epoch 1/100
18097/18097 [==============================] - 1s 78us/sample - loss: 0.7659 - accuracy: 0.7778 - val_loss: 0.4493 - val_accuracy: 0.8006
Epoch 2/100
18097/18097 [==============================] - 1s 43us/sample - loss: 0.4870 - accuracy: 0.8074 - val_loss: 0.4578 - val_accuracy: 0.7877
Epoch 3/100
18097/18097 [==============================] - 1s 45us/sample - loss: 3.2316 - accuracy: 0.6715 - val_loss: 11.5069 - val_accuracy: 0.2491
Epoch 4/100
18097/18097 [==============================] - 1s 47us/sample - loss: 11.5541 - accuracy: 0.2463 - val_loss: 11.5063 - val_accuracy: 0.2491
Epoch 5/100
18097/18097 [==============================] - 1s 43us/sample - loss: 10.5312 - accuracy: 0.2988 - val_loss: 5.6752 - val_accuracy: 0.5848
Epoch 6/100
18097/18097 [==============================

[CV] ......................... n_neurons=19, n_hidden=2, total=   9.9s


[Parallel(n_jobs=1)]: Done  30 out of  30 | elapsed:  8.7min finished


RuntimeError: Cannot clone object <tensorflow.python.keras.wrappers.scikit_learn.KerasClassifier object at 0x0000008D5FD92080>, as the constructor either does not set or modifies parameter n_neurons

In [60]:
rnd_search_cv.best_params_

{'n_neurons': 12, 'n_hidden': 2}

# Zad

Wykonaj RandomizedSearchCV na danych FashionMINT
